In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
from matplotlib.colors import LinearSegmentedColormap
from scipy.interpolate import griddata
import matplotlib.gridspec as gridspec

# Folders to process
folders = ["AA", "AR", "AAR", "Inner", "Outer"]

# Z values to select (bottom: 0.77, top: 2.31)
z_values = [2.31, 0.77]  # First row (top), second row (bottom)
#z_values = [0.55, 0.99]

#lim = [10, 0.5, .2, 0.1 , 0.01]

#new experimental limit
lim = [10, 1, 1.0e-4, 1.0e-8, 1.0e-16]

# Define custom color palette
colors = [
    (-lim[0], "darkgreen"),
    (-lim[1], "green"),
    (-lim[2], "lightgreen"),
    (-lim[3], "#98FB98"), # PaleGreen
    (-lim[4], "#7FFF00"), # Lemonyellow
    (0, "white"),
    (lim[4], "#FFB347"),
    (lim[3], "orange"),
    (lim[2], "darkorange"),
    (lim[1], "red"),
    (lim[0], "darkred"),
]

cmap_icc = LinearSegmentedColormap.from_list("custom_palette", [color[1] for color in colors])

# Normalize color range
vmin, vmax = -lim[0], lim[0]

# Create figure with GridSpec (ensuring equal subplot sizes)
fig = plt.figure(figsize=(18, 8), dpi=800)  # Adjusted figure width for better aspect ratio
gs = gridspec.GridSpec(2, 6, width_ratios=[1, 1, 1, 1, 1, 0.2], height_ratios=[1, 1])  # Reduced colorbar width

# Reduce gap between Z = 0.77 and Z = 2.31
#plt.subplots_adjust(wspace=0.10, hspace=0.02)  # Tight spacing

# Axes storage
axes = []

for col, folder in enumerate(folders):
    # Load dataset from the folder
    file_path = f"{folder}/potential_data.csv"
    full_df = pd.read_csv(file_path)

    for row, z_value in enumerate(z_values):
        # Filter data for the specific Z value
        filtered_df = full_df[full_df["Z"] == z_value]

        # Prepare data for interpolation
        x = filtered_df["X"]
        y = filtered_df["Y"]
        potential = filtered_df["Potential"]

        # Create a grid for the heatmap
        grid_x, grid_y = np.mgrid[min(x):max(x):1000j, min(y):max(y):1000j]

        # Interpolate data onto the grid
        grid_potential = griddata((x, y), potential, (grid_x, grid_y), method='linear')

        # Select the current axis
        ax = fig.add_subplot(gs[row, col])  # No extra space for Z labels
        axes.append(ax)

        # Plot heatmap without individual colorbars
        img = sns.heatmap(
            grid_potential,
            cmap=cmap_icc,
            vmin=vmin,
            vmax=vmax,
            cbar=False,  # Disable individual colorbars
            xticklabels=False,  # Remove x-tick labels
            yticklabels=False,  # Remove y-tick labels
            square=True,  # Ensures equal width and height for each subplot
            ax=ax
        )

        # Customize axes
        if col == 0:  # Show Y-axis label only once for "AA"
            y_ticks = np.arange(int(np.floor(min(y))), int(np.ceil(max(y))) + 1, 4)
            ax.set_yticks(np.linspace(0, grid_y.shape[0] - 1, len(y_ticks)))
            ax.set_yticklabels([f"{tick}" for tick in y_ticks], fontsize=16)

            if row == 0:  # Only add Y-axis label once
                ax.set_ylabel(r"$\longleftarrow$ $y$ (${\AA}$) $\longrightarrow$", fontsize=18, labelpad=10)  # Adjust label spacing
            else:
                ax.set_ylabel(r"$\longleftarrow$ $y$ (${\AA}$) $\longrightarrow$", fontsize=18, labelpad=10)  # Adjust label spacing
                #ax.set_ylabel("")
        else:
            ax.set_yticks([])
            ax.set_ylabel("")

        if row == 1:  # Show x-ticks & labels only for z = 0.77
            x_ticks = np.arange(int(np.floor(min(x))), int(np.ceil(max(x))) + 1, 4)
            ax.set_xticks(np.linspace(0, grid_x.shape[1] - 1, len(x_ticks)))
            ax.set_xticklabels([f"{tick}" for tick in x_ticks], fontsize=16)
            ax.set_xlabel(r"$\longleftarrow$ $x$ (${\AA}$) $\longrightarrow$", fontsize=18)
        else:
            ax.set_xticks([])
            ax.set_xlabel("")

        # Set title for each column
        if row == 0:
            ax.set_title(folder, fontsize=20)

# Create a separate colorbar on the right side with reduced width
cbar_ax = fig.add_subplot(gs[:, -1])  # Use the last column for the colorbar
cb = fig.colorbar(img.collections[0], cax=cbar_ax)
cb.ax.tick_params(labelsize=16)
cb.set_label("Electric Potential (V)", fontsize=18)

# Reduce white space between subplots while maintaining clarity
plt.subplots_adjust(wspace=0.15, hspace=-0.25)  # Tight spacing

# Save the figure
#plt.savefig("panel_heatmap_alternate_layer.png", dpi=800, bbox_inches="tight")

# Show the figure
plt.show()
